# Grab some sample data from flickr API

In this notebook, we use the Flickr API to obtain nearly randomly selected photo and user IDs. We use this information to query EXIF data through the API. The goal is to obtain a large sample dataset to be able to conduct further investigations.

In [11]:
# Python modules
import flickrapi
import pandas as pd
import requests
import json
import time
import os
from datetime import date
from dotenv import load_dotenv
load_dotenv()
from datetime import datetime
import googlemaps
import random

# Import additional functions
from flickr_functions import df_remove_dupes

# Keys needed for API access
api_key = os.getenv('flickr_api_key')
api_secret = os.getenv('flickr_api_secret')
maps_api_key = os.getenv('maps_api_key')

# Configure maps access
gmaps = googlemaps.Client(key=maps_api_key)

# Flickr API object
flickr = flickrapi.FlickrAPI(api_key, api_secret, format='parsed-json')

# Data directory used to store CVS files
data_dir = './data/'

In [12]:
# Define the dataframes and lists with columns

df_photo_ids = pd.DataFrame(columns = ['id', 
                                       'owner', 
                                       'secret', 
                                       'title', 
                                       'ispublic'])

columns_df_photo_exif = ['id', 'Image Width', 'Image Height', 'Compression', 'Make', 'Model',
       'Orientation', 'Software', 'Date and Time (Modified)', 'Exposure',
       'Aperture', 'ISO Speed', 'Date and Time (Original)',
       'Date and Time (Digitized)', 'Flash', 'Focal Length', 'White Balance',
       'owner', 'secret', 'title', 'lat', 'lon', 'acc', 'country', 'admin_lvl1', 'admin_lvl2', 'city']

df_photo_exif = pd.DataFrame(columns = columns_df_photo_exif)

## Harvest image and user IDs, use IDs to query for EXIF and geo data

In [21]:
# Get some nice random words from an API

languages = ['en', 'it', 'de', 'es']

URL='https://random-word-api.herokuapp.com/word?number='

def get_words(number, length):
    response = requests.get(URL + str(number) + '&length=' + str(length) + '&lang=' + random.choice(languages)).text
    return json.loads(response)

In [28]:
# Iterate through words, query API for results containing this word, add to dataframe

df_exif = pd.read_csv(data_dir + 'df_photo_exif_final.csv', index_col=[0])

df_photo_ids = pd.DataFrame(columns = ['id', 
                                       'owner', 
                                       'secret', 
                                       'title', 
                                       'ispublic'])

# start timer
start_time = time.time()

# count the number of added entries
counter = 0

for word in get_words(100, 5):

    print(word)

    try:
        get_photos = flickr.photos.search(text = word,
                        privacy_filter = 1, 
                        content_types = 0,
                        page = 1,
                        per_page = 500,
                        has_geo = 1)
    except flickrapi.exceptions.FlickrError as ex:
        print("Error code: %s" % ex.code)
    
    for photo in get_photos.get('photos').get('photo'):
        df_photo_ids.loc[len(df_photo_ids)] = {'id': photo.get('id'), 
                                            'owner': photo.get('owner'),
                                            'secret': photo.get('secret'),
                                            'title': photo.get('title'),
                                            'ispublic': photo.get('ispublic')}
        counter += 1
    
# end the timer and calculate duration
end_time = time.time()
minutes, seconds = divmod(int(end_time - start_time), 60)

#print(f'Fetched {counter} entries in {minutes} minutes and {seconds} seconds. Dataframe is now {len(df_photo_ids)} rows long.')

# Remove duplicates
df_photo_ids = df_remove_dupes(df_photo_ids)

# Look for ids that are in the exif file already (and drop them)
length_before = len(df_photo_ids)
df_photo_ids = df_photo_ids[~df_photo_ids.id.isin(df_exif.id)]
print(f'Removed {length_before - len(df_photo_ids)} entries because they are in the exif file already.')

# Iterate through dataframe, query API for EXIF data and add to another dataframe (and csv!)
length = len(df_photo_ids)
print(f'Number of rows of dataframe: {length}')

# start timer
start_time = time.time()

# Count the number of added entries
counter = 0

for i, row in df_photo_ids.iterrows():

    # Query the API
    try:
        exif_data = flickr.photos.getExif(photo_id = row['id'], photo_secret = 'secret').get('photo').get('exif')

        # Print counter
        print(f'{datetime.now().strftime("%H:%M:%S")}: Added entry {counter}: {row["id"]}, {row["title"]} | {length - counter} remaining')
        
        # Temporary dict
        dict_tmp = {}

        # Go through every EXIF key value pair available and add to tmp dict
        for exif in exif_data:
            key = exif.get('label')
            value = exif.get('raw').get('_content')
            dict_tmp[key] = value

        # Add ID from ID dataframe
        dict_tmp.update({'id': row['id']})
        dict_tmp.update({'owner': row['owner']})
        dict_tmp.update({'secret': row['secret']})
        dict_tmp.update({'title': row['title']})
        
        # Look for geodata and add it
        try:
            geodata = flickr.photos.geo.getLocation(photo_id = row['id'])

            lat = geodata.get('photo').get('location').get('latitude')
            lon = geodata.get('photo').get('location').get('longitude')
            acc = geodata.get('photo').get('location').get('accuracy')

            dict_tmp.update({'lat': lat})
            dict_tmp.update({'lon': lon})
            dict_tmp.update({'acc': acc})

            # Look up reverse geocoding by querying maps API

            country, admin_lvl1, admin_lvl2, city = '', '', '', ''

            # Query the API with the location data
            try:
                geo = gmaps.reverse_geocode((lat, lon))

                # Get the data from the response
                for comp in geo[0].get('address_components'):
                    if 'country' in comp.get('types'):
                        country = comp.get('long_name')
                    if 'administrative_area_level_1' in comp.get('types'):
                        admin_lvl1 = comp.get('long_name')
                    if 'administrative_area_level_2' in comp.get('types'):
                        admin_lvl2 = comp.get('long_name')
                    if 'locality' in comp.get('types'):
                        city = comp.get('long_name')
                    elif 'postal_town' in comp.get('types'):
                        city = comp.get('long_name')

                dict_tmp.update({'country': country})
                dict_tmp.update({'admin_lvl1': admin_lvl1})
                dict_tmp.update({'admin_lvl2': admin_lvl2})
                dict_tmp.update({'city': city})

                print(f'Added geodata: {lat}, {lon} in {country}, {admin_lvl1}, {admin_lvl2}, {city}')
                
            except googlemaps.exceptions.ApiError as err :
                print('API key is invalid')

                dict_tmp.update({'country': 'na'})
                dict_tmp.update({'admin_lvl1': 'na'})
                dict_tmp.update({'admin_lvl2': 'na'})
                dict_tmp.update({'city': 'na'})


        except flickrapi.exceptions.FlickrError as ex:

            # Add n/a if there's no geodata
            dict_tmp.update({'lat': 'na'})
            dict_tmp.update({'lon': 'na'})
            dict_tmp.update({'acc': 'na'})
            dict_tmp.update({'country': 'na'})
            dict_tmp.update({'admin_lvl1': 'na'})
            dict_tmp.update({'admin_lvl2': 'na'})
            dict_tmp.update({'city': 'na'})

            print(f'!!! Geo: Error code: {ex.code} for id {row["id"]}')

        # Add to dataframe
        df_photo_exif.loc[len(df_photo_exif)] = dict_tmp

        # Filename of csv to add data to
        filename = './data/df_photo_exif_final.csv'
        #filename = './data/df_photo_exif_final_bak.csv'
        
        # Create a temporary dataframe
        df_tmp = pd.DataFrame(columns = columns_df_photo_exif)
        df_tmp.loc[len(df_tmp)] = dict_tmp

        # If there is not enough information in dataset, do not add to csv
        #if len(df_tmp[df_tmp.count(axis='columns') >= 5]) > 0:
        df_tmp.to_csv(filename, mode='a', header=not os.path.exists(filename))
        #else:
        #    print('Not enough data, sry.')

    except flickrapi.exceptions.FlickrError as ex:
        print(f'!!! Error code: {ex.code} for id {row["id"]}')
    
    # Delete row from photo id dataframe
    df_photo_ids = df_photo_ids.drop(i)

    counter += 1

# end the timer and calculate duration
end_time = time.time()
minutes, seconds = divmod(int(end_time - start_time), 60)
per_hour = counter / (end_time - start_time) * 3600

print(f'Fetched {counter} entries in {minutes} minutes and {seconds} seconds ({per_hour} per hour).')

oorie
mixup
thirl
feces
fidos
rices
shews
merde
redux
cower
hight
aspen
forts
lurid
tsked
being
cohog
jived
duads
jinni
burds
klong
antsy
films
soots
perry
boozy
perms
eagle
coney
fluty
jalop
fakir
masas
knits
serif
clast
pates
ovine
dunch
clans
swiss
trios
named
wader
tango
ryked
slier
plonk
selfs
geste
bonze
derry
loams
bonny
yogic
suets
hurry
asana
creak
galop
veals
misdo
adman
burps
poufs
elude
cauld
expel
steek
round
skull
clave
tours
jimmy
sards
writs
serum
oxime
signa
braze
vuggy
skyey
dinos
proso
pooch
brads
icier
attar
sears
resin
freer
songs
muzzy
stirk
gnars
enate
speak
tunas
knobs
Found 190 duplicates. Dataframe is now 21474 rows long.
Removed 0 entries because they are in the exif file already.
Number of rows of dataframe: 21474
18:55:54: Added entry 0: 53163228695, Fort Horton: once a Union fortification in Louisville, now a park | 21474 remaining
Added geodata: 38.223427, -85.745881 in United States, Kentucky, Jefferson County, Louisville
18:55:55: Added entry 1: 5314801

do_request: Status code 500 received, content:
    <!DOCTYPE html>
<html xmlns:cc="http://creativecommons.org/ns#" lang="en-us" class="no-js fluid html-error-500-page-view scrolling-layout ">
<head>
	<meta property="og:site_name" content="Flickr" />
	<meta property="og:updated_time" content="2023-09-18T17:39:45.749Z" />
	
	<script type="application/ld+json">
		[{
			"@context": "http://schema.org",
			"@type": "WebSite",
			"name": "Flickr",
			"url": "https://www.flickr.com",
			"potentialAction": {
				"@type": "SearchAction",
				"target": "https://www.flickr.com/search?text={search_term_string}
    structured=yes",
				"query-input": "required name=search_term_string"
			}
		},
		{
			"@context": "http://schema.org",
			"@type": "Organization",
			"url": "http://www.flickr.com",
			"logo": "https://www.flickr.com/images/opensearch-flickr-logo.png"
		},
		{
			"@context": "http://schema.org",
			"@type": "Person",
			"name": "Flickr",
			"url": "https://www.flickr.com",
			"sameAs":

!!! Error code: None for id 53000444135
19:39:46: Added entry 3833: 53000543453, Rim Klong Ratchamontri Photo Walk | 17641 remaining


do_request: Status code 500 received, content:
    <!DOCTYPE html>
<html xmlns:cc="http://creativecommons.org/ns#" lang="en-us" class="no-js fluid html-error-500-page-view scrolling-layout ">
<head>
	<meta property="og:site_name" content="Flickr" />
	<meta property="og:updated_time" content="2023-09-18T17:39:46.578Z" />
	
	<script type="application/ld+json">
		[{
			"@context": "http://schema.org",
			"@type": "WebSite",
			"name": "Flickr",
			"url": "https://www.flickr.com",
			"potentialAction": {
				"@type": "SearchAction",
				"target": "https://www.flickr.com/search?text={search_term_string}
    structured=yes",
				"query-input": "required name=search_term_string"
			}
		},
		{
			"@context": "http://schema.org",
			"@type": "Organization",
			"url": "http://www.flickr.com",
			"logo": "https://www.flickr.com/images/opensearch-flickr-logo.png"
		},
		{
			"@context": "http://schema.org",
			"@type": "Person",
			"name": "Flickr",
			"url": "https://www.flickr.com",
			"sameAs":

!!! Geo: Error code: None for id 53000543453
19:39:47: Added entry 3834: 53000444095, Rim Klong Ratchamontri Photo Walk | 17640 remaining
Added geodata: 13.717277, 100.425658 in Thailand, Krung Thep Maha Nakhon, , 
19:39:48: Added entry 3835: 53000222164, Rim Klong Ratchamontri Photo Walk | 17639 remaining
Added geodata: 13.715511, 100.425744 in Thailand, Krung Thep Maha Nakhon, , 
19:39:49: Added entry 3836: 53000444105, Rim Klong Ratchamontri Photo Walk | 17638 remaining
Added geodata: 13.715827, 100.425705 in Thailand, Krung Thep Maha Nakhon, , 


...

!!! Error code: None for id 8497836831
19:44:34: Added entry 4152: 8495233839, 52:365 Snow Day! | 17322 remaining
Added geodata: 41.217048, -98.251358 in United States, Nebraska, Merrick County, Palmer
19:44:34: Added entry 4153: 8319863327, Sandhill Cranes | 17321 remaining
Added geodata: 35.167493, -106.647119 in United States, New Mexico, Bernalillo County, Los Ranchos de Albuquerque
19:44:35: Added entry 4154: 8287606951, Antsy girls. | 17320 remaining
Added geodata: 42.242150, -97.014400 in United States, Nebraska, Wayne County, Wayne
19:44:36: Added entry 4155: 8282546608, North Bridge, study 1 | 17319 remaining
Added geodata: 55.951620, -3.187966 in United Kingdom, Scotland, Edinburgh, Edinburgh
19:44:37: Added entry 4156: 8200088547, 22-Ton Cap | 17318 remaining
Added geodata: 33.728783, -118.269624 in United States, California, Los Angeles County, Los Angeles
19:44:38: Added entry 4157: 8197799089, Westbound at Marshfield | 17317 remaining
Added geodata: 40.241880, -87.465441 

do_request: Status code 500 received, content:
    <!DOCTYPE html>
<html xmlns:cc="http://creativecommons.org/ns#" lang="en-us" class="no-js fluid html-error-500-page-view scrolling-layout ">
<head>
	<meta property="og:site_name" content="Flickr" />
	<meta property="og:updated_time" content="2023-09-18T17:47:10.925Z" />
	
	<script type="application/ld+json">
		[{
			"@context": "http://schema.org",
			"@type": "WebSite",
			"name": "Flickr",
			"url": "https://www.flickr.com",
			"potentialAction": {
				"@type": "SearchAction",
				"target": "https://www.flickr.com/search?text={search_term_string}
    structured=yes",
				"query-input": "required name=search_term_string"
			}
		},
		{
			"@context": "http://schema.org",
			"@type": "Organization",
			"url": "http://www.flickr.com",
			"logo": "https://www.flickr.com/images/opensearch-flickr-logo.png"
		},
		{
			"@context": "http://schema.org",
			"@type": "Person",
			"name": "Flickr",
			"url": "https://www.flickr.com",
			"sameAs":

!!! Geo: Error code: None for id 53190368908
19:47:11: Added entry 4360: 53190321338, Sienna Miller x VOGUE World (London 2023) | 17114 remaining
Added geodata: 51.512628, -0.120345 in United Kingdom, England, Greater London, London
19:47:12: Added entry 4361: 53190152465, Sienna Miller x VOGUE World (London 2023) | 17113 remaining
Added geodata: 51.512628, -0.120345 in United Kingdom, England, Greater London, London
19:47:13: Added entry 4362: 53190321038, Sienna Miller x VOGUE World (London 2023) | 17112 remaining
Added geodata: 51.512628, -0.120345 in United Kingdom, England, Greater London, London
19:47:13: Added entry 4363: 53189744944, Maisie Williams x Candid Portraits Ltd | 17111 remaining
Added geodata: 51.512628, -0.120345 in United Kingdom, England, Greater London, London
19:47:14: Added entry 4364: 53189938946, Maisie Williams x Candid Portraits Ltd | 17110 remaining
Added geodata: 51.512628, -0.120345 in United Kingdom, England, Greater London, London
19:47:14: Added entry

do_request: Status code 500 received, content:
    <!DOCTYPE html>
<html xmlns:cc="http://creativecommons.org/ns#" lang="en-us" class="no-js fluid html-error-500-page-view scrolling-layout ">
<head>
	<meta property="og:site_name" content="Flickr" />
	<meta property="og:updated_time" content="2023-09-18T17:48:52.947Z" />
	
	<script type="application/ld+json">
		[{
			"@context": "http://schema.org",
			"@type": "WebSite",
			"name": "Flickr",
			"url": "https://www.flickr.com",
			"potentialAction": {
				"@type": "SearchAction",
				"target": "https://www.flickr.com/search?text={search_term_string}
    structured=yes",
				"query-input": "required name=search_term_string"
			}
		},
		{
			"@context": "http://schema.org",
			"@type": "Organization",
			"url": "http://www.flickr.com",
			"logo": "https://www.flickr.com/images/opensearch-flickr-logo.png"
		},
		{
			"@context": "http://schema.org",
			"@type": "Person",
			"name": "Flickr",
			"url": "https://www.flickr.com",
			"sameAs":

!!! Error code: None for id 53081109066
19:48:53: Added entry 4519: 53165814728, Lake Jocassee boat 7 Aug 17 23 | 16955 remaining
Added geodata: 34.984730, -82.971453 in United States, South Carolina, Oconee County, Salem
19:48:54: Added entry 4520: 53165754440, Lake Jocassee boat 5 Aug 17 23 | 16954 remaining
Added geodata: 34.982619, -82.945509 in United States, South Carolina, Oconee County, Salem
19:48:55: Added entry 4521: 53165159706, 000048440025-edit | 16953 remaining
Added geodata: 41.507980, -81.580558 in United States, Ohio, Cuyahoga County, Cleveland Heights
19:48:55: Added entry 4522: 53164565262, 000048440037-edit | 16952 remaining
Added geodata: 41.120292, -81.527287 in United States, Ohio, Summit County, Akron
19:48:56: Added entry 4523: 53165218175, Stormy Mediterranean sea | 16951 remaining
Added geodata: 35.956715, 14.424951 in Malta, , , San Pawl il-Baħar
19:48:57: Added entry 4524: 53164197237, Streets in Valletta | 16950 remaining
Added geodata: 35.897882, 14.5154